##### genetic algorithm

In [1]:
import random as rd
from ctypes import *
from bitsets import bitset
from bitarray import bitarray
import bitstring

In [18]:
class GeneticAlgorithm():
    
    def __init__(self, x_min, x_max, z_min, z_max, m, pop_c, prob):
        self.x_min = x_min
        self.x_max = x_max
        self.z_min = z_min
        self.z_max = z_max
        self.mutation_probability = m  #вероятность мутации
        self.population_count = pop_c  #население
        self.cross_probability = prob  #вероятность скрещивания
        
        step_x = (self.x_max - self.x_min) / self.population_count         #шаг по оси х
        step_z = (self.z_max - self.z_min) / self.population_count         #шаг по оси y
         
        self.data = []       #храним пары [x, y]
        self.res  = []       #храним результаты из функции

        for idx in range(0, self.population_count):
            self.data.append([self.x_min + step_x * idx, self.z_min + step_z * idx]);
            self.res.append(self.function(self.data[idx][0], self.data[idx][1]));
    
    def tournamentSelection(self):
        buff = []
        rb = []

        while len(buff) != self.population_count:
        
            t1 = rd.randint(0, 10000) % len(self.data)
            t2 = rd.randint(0, 10000) % len(self.data)

            if self.res[t1] > self.res[t2]:
                buff.append(self.data[t1])
                rb.append(self.res[t1])

                self.data[t1], self.data[-1] = self.data[-1], self.data[t1] 
                self.res[t1],  self.res[-1]  = self.res[-1],  self.res[t1]
                self.data.pop()
                self.res.pop()
            else:
                buff.append(self.data[t2])
                rb.append(self.res[t2])

                self.data[t2], self.data[-1] = self.data[-1], self.data[t2] 
                self.res[t2],  self.res[-1]  = self.res[-1],  self.res[t2]
                self.data.pop()
                self.res.pop()

        self.data = buff
        self.res  = rb
        
        
    def function(self, x, z):
        return float(-(x * x + z * z))

    def kill(self, c1, c2):
        if (c1[0] > self.x_max or c1[0] < self.x_min or c1[1] > self.z_max or c1[1] < self.z_min 
        or  c2[0] > self.x_max or c2[0] < self.x_min or c2[1] > self.z_max or c2[1] < self.z_min):
            return True
        else:
            return False
    
    
    def searchBest(self):
        color = [False] * len(self.data)       #закрашиваем тех, кого скрестили
                                               #используем случайный выбор для кроссинговера
        for k in range(0, self.population_count):
            j = rd.randint(0, 100000) % self.population_count
            i = rd.randint(0, 100000) % self.population_count

            if color[i] == False:
                b1 = self.data[j]
                b2 = self.data[i]
                self.crossingOver(b1, b2)

                if (self.kill(b1, b2) == False):
                    self.data.append(b1)
                    self.data.append(b2)
                    self.res.append(self.function(b1[0], b1[1]))
                    self.res.append(self.function(b2[0], b2[1]))
            
                color[i] = True
                color[j] = True
        #после скрещивания надо провести отбор
        self.tournamentSelection()
    
    def mutation(self, c):
        class actual_data( Union ):
            _fields_ = [( "in_", c_float ), ( 'out_', c_ulong )]
        uni = actual_data()

        uni.in_ = c
        f1 = bitstring.BitArray(float = uni.out_, length = 32) 
        bi = f1.bin
        a = bitarray(bi)

        pred = rd.randint(0, 100000) % 1000 / 1000;

        if pred < self.mutation_probability:
            idx = rd.randint(0, 100000) % 31
            a[idx] = 0 if (a[idx] == 1) else 1
            uni.out_ = int(a.to01(), 2)

        return uni.in_
    
    
    def crossingOver(self, cop_1, cop_2):
        for i in 0, 1:
            class actual_data( Union ):
                _fields_ = [( "in_", c_float ), ( 'out_', c_ulong )]
            uni_1 = actual_data()
            uni_2 = actual_data()

#             print(uni_1.in_, uni_1.out_)
            
            uni_1.in_ = cop_1[i]
            uni_2.in_ = cop_2[i]
            print("до", uni_1.in_, uni_2.in_, uni_1.out_, uni_2.out_)

            f1 = bitstring.BitArray(float = uni_1.out_, length = 32) 
            bi1 = f1.bin
            bits_1 = bitarray(bi1)
            bits_1_buff = bitarray(bi1)
            print("bits1", bits_1, bits_1_buff)
            
            f2 = bitstring.BitArray(float = uni_2.out_, length = 32)
            bi2 = f2.bin
            bits_2 = bitarray(bi2)
            bits_2_buff = bitarray(bi2)
            print("bits2", bits_2, bits_2_buff)

            print("buff do   ", bits_1_buff, bits_2_buff)

            flag = rd.randint(0, 100000) % 31
            for j in range(flag, 0, -1):
                bits_2_buff[j] = bits_1[j]
                bits_1_buff[j] = bits_2[j]
            
            
            print("buff после", bits_1_buff, bits_2_buff)
            uni_1.out_ = int(bits_1_buff.to01(), 2)
            uni_2.out_ = int(bits_2_buff.to01(), 2)
            
            print("out после", uni_1.out_, uni_2.out_)

            
            print("in после", uni_1.in_, uni_2.in_)
            
            cop_1[i] = self.mutation(float(uni_1.in_))
            cop_2[i] = self.mutation(float(uni_2.in_))
            print("после", cop_1[i], cop_2[i])
            print()
    
    def result(self):
        x = 0
        y = 0
        result = -2147483648

        for i in range(0, len(self.data)):
            if self.res[i] > result:
                x = self.data[i][0]
                y = self.data[i][1]
                result = self.res[i]

#         return {x, y, result}
        return {'x': x, 'y': y, "result": result}


In [19]:
test = GeneticAlgorithm(0, 10, 0, 10, 0, 100, 1)

In [20]:
for i in range(0, 100):
    test.searchBest()

до 2.200000047683716 1.5 1074580685 1069547520
bits1 bitarray('01001110100000000001100110011010') bitarray('01001110100000000001100110011010')
bits2 bitarray('01001110011111110000000000000000') bitarray('01001110011111110000000000000000')
buff do    bitarray('01001110100000000001100110011010') bitarray('01001110011111110000000000000000')
buff после bitarray('01001110100000000001100110011010') bitarray('01001110011111110000000000000000')
out после 1317018010 1316945920
in после 1074580736.0 1069547520.0
после 1074580736.0 1069547520.0

до 2.200000047683716 1.5 1074580685 1069547520
bits1 bitarray('01001110100000000001100110011010') bitarray('01001110100000000001100110011010')
bits2 bitarray('01001110011111110000000000000000') bitarray('01001110011111110000000000000000')
buff do    bitarray('01001110100000000001100110011010') bitarray('01001110011111110000000000000000')
buff после bitarray('01001110100000000001100110011010') bitarray('01001110011111110000000000000000')
out после 13170180

до 1320157184.0 0.6000000238418579 1318936576 1058642330
bits1 bitarray('01001110100111010011101011000000') bitarray('01001110100111010011101011000000')
bits2 bitarray('01001110011111000110011001100110') bitarray('01001110011111000110011001100110')
buff do    bitarray('01001110100111010011101011000000') bitarray('01001110011111000110011001100110')
buff после bitarray('01001110000111010011101011000000') bitarray('01001110111111000110011001100110')
out после 1310538432 1325164134
in после 659468288.0 2117284608.0
после 659468288.0 2117284608.0

до 1085276160.0 0.6000000238418579 1317101568 1058642330
bits1 bitarray('01001110100111010000001011000000') bitarray('01001110100111010000001011000000')
bits2 bitarray('01001110011111000110011001100110') bitarray('01001110011111000110011001100110')
buff do    bitarray('01001110100111010000001011000000') bitarray('01001110011111000110011001100110')
buff после bitarray('01001110011111010000001011000000') bitarray('01001110100111000110011001100110')


buff после bitarray('01001110100111010011101000001001') bitarray('01001110100111010000001100001101')
out после 1318926857 1318912781
in после 1318913152.0 1317111424.0
после 1318913152.0 1317111424.0

до 1056964608.0 1066192064.0 1316749312 1316893491
bits1 bitarray('01001110100111001111100000000000') bitarray('01001110100111001111100000000000')
bits2 bitarray('01001110100111001111110001100110') bitarray('01001110100111001111110001100110')
buff do    bitarray('01001110100111001111100000000000') bitarray('01001110100111001111110001100110')
buff после bitarray('01001110100111001111110000000000') bitarray('01001110100111001111100001100110')
out после 1318910976 1318910054
in после 1316880384.0 1316762368.0
после 1316880384.0 1316762368.0

до 1045220352.0 1066192064.0 1316565808 1316893491
bits1 bitarray('01001110100111001111001001100110') bitarray('01001110100111001111001001100110')
bits2 bitarray('01001110100111001111110001100110') bitarray('01001110100111001111110001100110')
buff do    

до 1318912640.0 1090655872.0 1318926853 1317143597
bits1 bitarray('01001110100111010011101001110100') bitarray('01001110100111010011101001110100')
bits2 bitarray('01001110100111010000010000001000') bitarray('01001110100111010000010000001000')
buff do    bitarray('01001110100111010011101001110100') bitarray('01001110100111010000010000001000')
buff после bitarray('01001110100111010011101001110100') bitarray('01001110100111010000010000001000')
out после 1318926964 1318913032
in после 1318926848.0 1317143552.0
после 1318926848.0 1317143552.0

до 1317089536.0 1317154816.0 1318912610 1318913120
bits1 bitarray('01001110100111010011101000000101') bitarray('01001110100111010011101000000101')
bits2 bitarray('01001110100111010011101000001001') bitarray('01001110100111010011101000001001')
buff do    bitarray('01001110100111010011101000000101') bitarray('01001110100111010011101000001001')
buff после bitarray('01001110100111010011101000000101') bitarray('01001110100111010011101000001001')
out после 

buff do    bitarray('01001110100111010011101001110100') bitarray('01001110100111010011101000000000')
buff после bitarray('01001110100111010011101001110100') bitarray('01001110100111010011101000000000')
out после 1318926964 1318926848
in после 1318926848.0 1318912000.0
после 1318926848.0 1318912000.0

до 1317086336.0 1287441664.0 1318912585 1318680986
bits1 bitarray('01001110100111010011101000000101') bitarray('01001110100111010011101000000101')
bits2 bitarray('01001110100111010011001011110011') bitarray('01001110100111010011001011110011')
buff do    bitarray('01001110100111010011101000000101') bitarray('01001110100111010011001011110011')
buff после bitarray('01001110100111010011101000000101') bitarray('01001110100111010011001011110011')
out после 1318926853 1318925043
in после 1318912640.0 1318680960.0
после 1318912640.0 1318680960.0

до 1318912768.0 1717567488.0 1318926854 1322041344
bits1 bitarray('01001110100111010011101001110100') bitarray('01001110100111010011101001110100')
bits2 

...

buff do    bitarray('01001110100111010011101001110101') bitarray('01001110100111010011101001110101')
buff после bitarray('01001110100111010011101001110101') bitarray('01001110100111010011101001110101')
out после 1318926965 1318926965
in после 1318926976.0 1318926976.0
после 1318926976.0 1318926976.0

до 1318926976.0 1318926976.0 1318926965 1318926965
bits1 bitarray('01001110100111010011101001110101') bitarray('01001110100111010011101001110101')
bits2 bitarray('01001110100111010011101001110101') bitarray('01001110100111010011101001110101')
buff do    bitarray('01001110100111010011101001110101') bitarray('01001110100111010011101001110101')
buff после bitarray('01001110100111010011101001110101') bitarray('01001110100111010011101001110101')
out после 1318926965 1318926965
in после 1318926976.0 1318926976.0
после 1318926976.0 1318926976.0

до 1318926976.0 1318926976.0 1318926965 1318926965
bits1 bitarray('01001110100111010011101001110101') bitarray('01001110100111010011101001110101')
bits2 

после 1318926976.0 1318926976.0

до 1318926976.0 1318926976.0 1318926965 1318926965
bits1 bitarray('01001110100111010011101001110101') bitarray('01001110100111010011101001110101')
bits2 bitarray('01001110100111010011101001110101') bitarray('01001110100111010011101001110101')
buff do    bitarray('01001110100111010011101001110101') bitarray('01001110100111010011101001110101')
buff после bitarray('01001110100111010011101001110101') bitarray('01001110100111010011101001110101')
out после 1318926965 1318926965
in после 1318926976.0 1318926976.0
после 1318926976.0 1318926976.0

до 1318926976.0 1318926976.0 1318926965 1318926965
bits1 bitarray('01001110100111010011101001110101') bitarray('01001110100111010011101001110101')
bits2 bitarray('01001110100111010011101001110101') bitarray('01001110100111010011101001110101')
buff do    bitarray('01001110100111010011101001110101') bitarray('01001110100111010011101001110101')
buff после bitarray('01001110100111010011101001110101') bitarray('010011101001

bits2 bitarray('01001110100111010011101001110101') bitarray('01001110100111010011101001110101')
buff do    bitarray('01001110100111010011101001110101') bitarray('01001110100111010011101001110101')
buff после bitarray('01001110100111010011101001110101') bitarray('01001110100111010011101001110101')
out после 1318926965 1318926965
in после 1318926976.0 1318926976.0
после 1318926976.0 1318926976.0

до 1318926976.0 1318926976.0 1318926965 1318926965
bits1 bitarray('01001110100111010011101001110101') bitarray('01001110100111010011101001110101')
bits2 bitarray('01001110100111010011101001110101') bitarray('01001110100111010011101001110101')
buff do    bitarray('01001110100111010011101001110101') bitarray('01001110100111010011101001110101')
buff после bitarray('01001110100111010011101001110101') bitarray('01001110100111010011101001110101')
out после 1318926965 1318926965
in после 1318926976.0 1318926976.0
после 1318926976.0 1318926976.0

до 1318926976.0 1318926976.0 1318926965 1318926965
bits1 

in после 1318926976.0 1318926976.0
после 1318926976.0 1318926976.0

до 1318926976.0 1318926976.0 1318926965 1318926965
bits1 bitarray('01001110100111010011101001110101') bitarray('01001110100111010011101001110101')
bits2 bitarray('01001110100111010011101001110101') bitarray('01001110100111010011101001110101')
buff do    bitarray('01001110100111010011101001110101') bitarray('01001110100111010011101001110101')
buff после bitarray('01001110100111010011101001110101') bitarray('01001110100111010011101001110101')
out после 1318926965 1318926965
in после 1318926976.0 1318926976.0
после 1318926976.0 1318926976.0

до 1318926976.0 1318926976.0 1318926965 1318926965
bits1 bitarray('01001110100111010011101001110101') bitarray('01001110100111010011101001110101')
bits2 bitarray('01001110100111010011101001110101') bitarray('01001110100111010011101001110101')
buff do    bitarray('01001110100111010011101001110101') bitarray('01001110100111010011101001110101')
buff после bitarray('0100111010011101001110

bits1 bitarray('01001110100111010011101001110101') bitarray('01001110100111010011101001110101')
bits2 bitarray('01001110100111010011101001110101') bitarray('01001110100111010011101001110101')
buff do    bitarray('01001110100111010011101001110101') bitarray('01001110100111010011101001110101')
buff после bitarray('01001110100111010011101001110101') bitarray('01001110100111010011101001110101')
out после 1318926965 1318926965
in после 1318926976.0 1318926976.0
после 1318926976.0 1318926976.0

до 1318926976.0 1318926976.0 1318926965 1318926965
bits1 bitarray('01001110100111010011101001110101') bitarray('01001110100111010011101001110101')
bits2 bitarray('01001110100111010011101001110101') bitarray('01001110100111010011101001110101')
buff do    bitarray('01001110100111010011101001110101') bitarray('01001110100111010011101001110101')
buff после bitarray('01001110100111010011101001110101') bitarray('01001110100111010011101001110101')
out после 1318926965 1318926965
in после 1318926976.0 1318926

In [21]:
print(test.result())

{'x': 1318926976.0, 'y': 1318926976.0, 'result': -0.0}
